# Data drift dashboard in jupyter notebook

In [1]:
import pandas as pd
import numpy as np
import requests
import zipfile
import io

from datetime import datetime
from sklearn import datasets, ensemble

from evidently.dashboard import Dashboard
from evidently.pipeline.column_mapping import ColumnMapping
from evidently.dashboard.tabs import DataDriftTab, NumTargetDriftTab, RegressionPerformanceTab

## Bicycle Demand Data

In [2]:
content = requests.get("https://archive.ics.uci.edu/ml/machine-learning-databases/00275/Bike-Sharing-Dataset.zip").content
with zipfile.ZipFile(io.BytesIO(content)) as arc:
    raw_data = pd.read_csv(arc.open("hour.csv"), header=0, sep=',', parse_dates=['dteday'], index_col='dteday')

In [3]:
#raw_data = pd.read_csv('~/Dev/evidently/train.csv', header=0, sep=',', parse_dates=['datetime'], index_col='datetime')

In [4]:
raw_data.head()

instant  season  yr  mnth  hr  holiday  weekday  workingday  \
dteday                                                                    
2011-01-01        1       1   0     1   0        0        6           0   
2011-01-01        2       1   0     1   1        0        6           0   
2011-01-01        3       1   0     1   2        0        6           0   
2011-01-01        4       1   0     1   3        0        6           0   
2011-01-01        5       1   0     1   4        0        6           0   

            weathersit  temp   atemp   hum  windspeed  casual  registered  cnt  
dteday                                                                          
2011-01-01           1  0.24  0.2879  0.81        0.0       3          13   16  
2011-01-01           1  0.22  0.2727  0.80        0.0       8          32   40  
2011-01-01           1  0.22  0.2727  0.80        0.0       5          27   32  
2011-01-01           1  0.24  0.2879  0.75        0.0       3          10   13  
2011-01-01           1  0.24  0.2879  0.75        0.0       0           1    1

## Regression Model

### Feature engineering

In [5]:
raw_data['month'] = raw_data.index.map(lambda x : x.month)
raw_data['hour'] = raw_data.index.map(lambda x : x.hour)
raw_data['weekday'] = raw_data.index.map(lambda x : x.weekday() + 1)

In [6]:
raw_data.head()

instant  season  yr  mnth  hr  holiday  weekday  workingday  \
dteday                                                                    
2011-01-01        1       1   0     1   0        0        6           0   
2011-01-01        2       1   0     1   1        0        6           0   
2011-01-01        3       1   0     1   2        0        6           0   
2011-01-01        4       1   0     1   3        0        6           0   
2011-01-01        5       1   0     1   4        0        6           0   

            weathersit  temp   atemp   hum  windspeed  casual  registered  \
dteday                                                                      
2011-01-01           1  0.24  0.2879  0.81        0.0       3          13   
2011-01-01           1  0.22  0.2727  0.80        0.0       8          32   
2011-01-01           1  0.22  0.2727  0.80        0.0       5          27   
2011-01-01           1  0.24  0.2879  0.75        0.0       3          10   
2011-01-01           1  0.24  0.2879  0.75        0.0       0           1   

            cnt  month  hour  
dteday                        
2011-01-01   16      1     0  
2011-01-01   40      1     0  
2011-01-01   32      1     0  
2011-01-01   13      1     0  
2011-01-01    1      1     0

### Model training

In [7]:
target = 'cnt'
prediction = 'prediction'
numerical_features = ['temp', 'atemp', 'hum', 'windspeed', 'hour', 'weekday']
categorical_features = ['season', 'holiday', 'workingday']

In [8]:
reference = raw_data.loc['2011-01-01 00:00:00':'2011-01-28 23:00:00']
current = raw_data.loc['2011-01-29 00:00:00':'2011-02-28 23:00:00']

In [9]:
reference.head()

instant  season  yr  mnth  hr  holiday  weekday  workingday  \
dteday                                                                    
2011-01-01        1       1   0     1   0        0        6           0   
2011-01-01        2       1   0     1   1        0        6           0   
2011-01-01        3       1   0     1   2        0        6           0   
2011-01-01        4       1   0     1   3        0        6           0   
2011-01-01        5       1   0     1   4        0        6           0   

            weathersit  temp   atemp   hum  windspeed  casual  registered  \
dteday                                                                      
2011-01-01           1  0.24  0.2879  0.81        0.0       3          13   
2011-01-01           1  0.22  0.2727  0.80        0.0       8          32   
2011-01-01           1  0.22  0.2727  0.80        0.0       5          27   
2011-01-01           1  0.24  0.2879  0.75        0.0       3          10   
2011-01-01           1  0.24  0.2879  0.75        0.0       0           1   

            cnt  month  hour  
dteday                        
2011-01-01   16      1     0  
2011-01-01   40      1     0  
2011-01-01   32      1     0  
2011-01-01   13      1     0  
2011-01-01    1      1     0

In [10]:
regressor = ensemble.RandomForestRegressor(random_state = 0, n_estimators = 50)

In [11]:
regressor.fit(reference[numerical_features + categorical_features], reference[target])

RandomForestRegressor(n_estimators=50, random_state=0)

In [12]:
ref_prediction = regressor.predict(reference[numerical_features + categorical_features])
current_prediction = regressor.predict(current[numerical_features + categorical_features])

In [13]:
reference['prediction'] = ref_prediction
current['prediction'] = current_prediction

### Model Perfomance 

In [14]:
column_mapping = ColumnMapping()

column_mapping.target = target
column_mapping.prediction = prediction
column_mapping.numerical_features = numerical_features
column_mapping.categorical_features = categorical_features

In [15]:
regression_perfomance_dashboard = Dashboard(tabs=[RegressionPerformanceTab()])
regression_perfomance_dashboard.calculate(reference, None, column_mapping=column_mapping)

In [16]:
regression_perfomance_dashboard.show()

In [17]:
#regression_perfomance_dashboard.save('reports/regression_performance_at_training.html')

##  Week 1

In [18]:
regression_perfomance_dashboard.calculate(reference, current.loc['2011-01-29 00:00:00':'2011-02-07 23:00:00'], 
                                            column_mapping=column_mapping)

In [19]:
regression_perfomance_dashboard.show()

In [20]:
#regression_perfomance_dashboard.save('reports/regression_performance_after_week1.html')

In [21]:
target_drift_dashboard = Dashboard(tabs=[NumTargetDriftTab()])
target_drift_dashboard.calculate(reference, current.loc['2011-01-29 00:00:00':'2011-02-07 23:00:00'], 
                                   column_mapping=column_mapping)

In [22]:
target_drift_dashboard.show()

In [23]:
#target_drift_dashboard.save('reports/target_drift_after_week1.html')

## Week 2

In [24]:
regression_perfomance_dashboard.calculate(reference, current.loc['2011-02-07 00:00:00':'2011-02-14 23:00:00'], 
                                            column_mapping=column_mapping)

In [25]:
regression_perfomance_dashboard.show()

In [26]:
#regression_perfomance_dashboard.save('reports/regression_performance_after_week2.html')

In [27]:
target_drift_dashboard.calculate(reference, current.loc['2011-02-07 00:00:00':'2011-02-14 23:00:00'], 
                                   column_mapping=column_mapping)

In [28]:
target_drift_dashboard.show()

In [29]:
#target_drift_dashboard.save('reports/target_drift_after_week2.html')

## Week 3

In [30]:
regression_perfomance_dashboard.calculate(reference, current.loc['2011-02-15 00:00:00':'2011-02-21 23:00:00'], 
                                            column_mapping=column_mapping)

In [31]:
regression_perfomance_dashboard.show()

In [32]:
#regression_perfomance_dashboard.save('reports/regression_performance_after_week3.html')

In [33]:
target_drift_dashboard.calculate(reference, current.loc['2011-02-15 00:00:00':'2011-02-21 23:00:00'], 
                                   column_mapping=column_mapping)

In [34]:
target_drift_dashboard.show()

In [35]:
#target_drift_dashboard.save('reports/target_drift_after_week3.html')

## Data Drift

In [36]:
column_mapping = ColumnMapping()

column_mapping.numerical_features = numerical_features

In [37]:
data_drift_dashboard = Dashboard(tabs=[DataDriftTab()])
data_drift_dashboard.calculate(reference, current.loc['2011-01-29 00:00:00':'2011-02-07 23:00:00'], 
                                   column_mapping=column_mapping)

In [38]:
data_drift_dashboard.show()

In [39]:
#data_drift_dashboard.save("reports/data_drift_dashboard_after_week1.html")